In [ ]:
## OpenSoundscape RIBBIT tutorial
# http://opensoundscape.org/en/latest/tutorials/RIBBIT_pulse_rate_demo.html

# Setup 

In [3]:
# suppress warnings
import warnings
warnings.simplefilter('ignore')
warnings.simplefilter('ignore', UserWarning)
    
#import packages
import numpy as np
from glob import glob
import pandas as pd
from matplotlib import pyplot as plt
import subprocess
from datetime import datetime
import os


#local imports from opensoundscape
from opensoundscape.audio import Audio
from opensoundscape.spectrogram import Spectrogram
from opensoundscape.ribbit import ribbit

# create big visuals
plt.rcParams['figure.figsize']=[15,8]
pd.set_option('display.precision', 2)

## Set base parameters 

These parameters can be adjusted to try to improve the model or to change the model for a different herp species 

### Current best parameters for gopher frog detection (as of December 2022): 
base_pulse_rate_range = [14,28] pulses per sec

base_signal_band = [600,800] Hz

*Note: gopher frogs CAN call outside this signal range; however, MML found that widening this range 
did not help capture more calls  - possibly because introducing too much noise? Worth investigating further?* 

base_noise_bands = [[150,200], [1100,1200]] Hz

base_clip_duration = 1 seconds

base_clip_overlap = 0.5 seconds

base_window_samples = 512

### Most sensitive parameters: 
signal_band, noise_band, window_samples

In [12]:
# minimum and maximum rate of pulsing (pulses per second) to search for
base_pulse_rate_range = [14,28] 

# look for a vocalization in the range of 600-800 Hz
base_signal_band = [600,800] 


# subtract the amplitude signal from these frequency ranges
base_noise_bands = [[150,200], [1100,1200]]

#divides the signal into segments this many seconds long, analyzes each independently
base_clip_duration = 1 #seconds
base_clip_overlap = 0.5 #seconds

# window_samples used to create spectrogram - default 512. smaller -> greater time resolution. bigger -> greater frequency resolution
base_window_samples = 512

#if True, it will show the power spectrum plot for each audio segment
show_plots = False # don't change this - will slow down model considerably 


## Functions to run RIBBIT 

In [13]:
# run RIBBIT for every index in a df where the index is a file path; save the score in that df 

# Inputs: 
# df - dataframe with filepaths to audio files as the indices of the dataframe
#      It is recommended that the dataframe includes columns with: 
#          - the year the file was recorded
#          - the date and time the file was recorded 
#          - any interesting groupings for the files (e.g. logger it was recorded with, pond/wetland where it was recorded, etc.)
# Parameters for the RIBBIT model: pulse_rate_range, singal_band, noise_bands, clip_duration, clip_overlap, window_samples 
#           Defaults are the base parameters defined above 
# param_set_lab - a label used when running multiple parameter sets (e.g. during sensitivity analysis (SA))
#       to indicate which set of parameters the "score" and "time_stamp" columns correspond to
#       blank if only running one set of parameters
# folder_lab - label for what the folder name should be where ribbit scores are saved. 
#       Folder will be labeled "ribbit_scores_folder_lab"

# Outputs: 
# ribbit_scores.csv - datasheet with Ribbit scores for each file 
# param_values.txt - text file with parameter values used for the model. 
# (if running multiple parameter sets, the csv and txt files will be labeled with param_set_lab)

def run_ribbit_for_indices(df, pulse_rate_range=base_pulse_rate_range,
                                signal_band=base_signal_band,
                                noise_bands=base_noise_bands, 
                                clip_duration=base_clip_duration,
                                clip_overlap=base_clip_overlap,
                                window_samples = base_window_samples, 
                                param_set_lab="", 
                                folder_lab = ''):
    
    folder_path = './ribbit_scores' + folder_lab
    if not os.path.exists(folder_path):
        os.makedirs(folder_path)
        
    csv_file_name = folder_path + '/ribbit_scores' + param_set_lab + '.csv'
    
    # Save a text file with the parameter values for future reference 
    param_file = open(folder_path + "/param_values" + param_set_lab + ".txt", "w") 
    str1 = repr(pulse_rate_range) 
    param_file.write("pulse_rate_range = " + str1 + "\n")
    str1 = repr(signal_band) 
    param_file.write("signal_band = " + str1 + "\n")
    str1 = repr(noise_bands) 
    param_file.write("noise_bands = " + str1 + "\n")
    str1 = repr(clip_duration) 
    param_file.write("clip_duration = " + str1 + "\n")
    str1 = repr(clip_overlap) 
    param_file.write("clip_overlap = " + str1 + "\n")
    str1 = repr(window_samples) 
    param_file.write("window_samples = " + str1 + "\n")
    param_file.close()
    
    start_time = datetime.now() # track how long the model takes
    checkpoint = 0; # create checkpoint for saving RIBBIT scores periodically 

    # for every file in the dataframe, calculate the RIBBIT score 
    for path in df.index:

        try: # make sure RIBBIT is working for this audio file, if it doesn't work for some reason, skip this so the model will continue running 
            #make the spectrogram
            spec = Spectrogram.from_audio(Audio.from_file(path), window_samples = window_samples)

            #run RIBBIT on the spectrogram with desired parameters 
            score_df =  ribbit(
                                spec,
                                pulse_rate_range=pulse_rate_range,
                                signal_band=signal_band,
                                clip_duration=clip_duration,
                                clip_overlap=clip_overlap,
                                noise_bands=noise_bands,
                                plot=False)


            maxIndex= score_df.score.idxmax() # find the index for where the max RIBBIT score occurs for the audio file 

            # record the max RIBBIT score for the auio file (multiplied by 10,000 to make it easier to read)
            df.at[path,'score'+param_set_lab] = score_df.at[maxIndex, 'score'] * 10000
            # record the time in the audio file that the max RIBBIT score occurs (so can be checked manually)
            df.at[path,'time_stamp'+param_set_lab] = score_df.at[maxIndex, 'start_time']

            checkpoint = checkpoint + 1 

        except (RuntimeError, EOFError) as runtime_error: # if the file does not work with RIBBIT, skip it and output a failure message; use -1 for RIBBIT score and time stamp
            print("File failed: ", path)
            print(runtime_error)


            df.at[path,'score'+param_set_lab] = -1 
            df.at[path,'time_stamp'+param_set_lab] = -1
            checkpoint = checkpoint + 1
            pass 

        # every 100 files, print checkpoint message and save RIBBIT scores to csv file to back them up 
        if checkpoint % 100 == 0:
            print("Finished file number ", checkpoint, "/nFile name: ", path)
            # print(df.sort_values(by='score'+param_set_lab,ascending=False).head(1))
            df.to_csv(csv_file_name) 


    df.sort_values(by='score'+param_set_lab,ascending=False).to_csv(csv_file_name) # sort by highest RIBBIT scores and save to csv
    print('Time elapsed ',datetime.now() - start_time) # print time taken to run model 
    
# ------------------------------------------------------------------------------------- #

# function to run OFAT sensitivity analysis (run multiple parameter sets changing only one parameter)

# Inputs: 
# df - dataframe with filepaths to audio files as the indices of the dataframe
# test_param - the name of the parameter that is varied (e.g. "pulse_rate_range")
# param_vals - the values you want to test for test_param
#       Note: all other values will default to the base parameters

# Outputs: 
# folder labeled "ribbit_scores_test_param" containing a csv file and txt file for each parameter set: 
#      ribbit_scores_####.csv - datasheet with Ribbit scores for each file
#      param_values_####.txt - text file with parameter values used for the model

def run_ribbit_SA(df, test_param, param_vals):
    if test_param == "pulse_rate_range":
        for p in range(0,len(param_vals)):
            run_ribbit_for_indices(df, pulse_rate_range = param_vals[p], 
                                   param_set_lab = str(p), folder_lab = "_"+test_param)
    elif test_param == "signal_band":
        for p in range(0,len(param_vals)):
            run_ribbit_for_indices(df, signal_band = param_vals[p], 
                                   param_set_lab = str(p), folder_lab = "_"+test_param)
    elif test_param == "noise_bands":
        for p in range(0,len(param_vals)):
            run_ribbit_for_indices(df, noise_bands = param_vals[p], 
                                   param_set_lab = str(p), folder_lab = "_"+test_param)
    elif test_param == "clip_duration":
        for p in range(0,len(param_vals)):
            run_ribbit_for_indices(df, clip_duration = param_vals[p], 
                                   param_set_lab = str(p), folder_lab = "_"+test_param)
    elif test_param == "clip_overlap":
        for p in range(0,len(param_vals)):
            run_ribbit_for_indices(df, clip_overlap = param_vals[p], 
                                   param_set_lab = str(p), folder_lab = "_"+test_param)
    elif test_param == "window_samples":
        for p in range(0,len(param_vals)):
            run_ribbit_for_indices(df, window_samples = param_vals[p], 
                                   param_set_lab = str(p), folder_lab = "_"+test_param)

    else: 
        print("Warning: test parameter not recognized")
        
        

# Running the model 

## How to use: 

1. Choose the base parameters you want to run your model in the **Set base parameters** section of this notebook. 
2. Run all **Setup** code chunks to prepare the model for use. 
3. Use the **Run Sandhills data** or **Run Ichaway data** code chunks to run the model. 
   1. Note: The file paths are those used by MML - file paths may differ slightly for different users. Edit the `folder=` line of code as needed to match your file path. 
   2. Edit `all_years` and/or `all_loggers` if you only want to run the model for specific years/loggers of data.
   3. These two code chunks should be adaptable to other datasets, as well - it just must be edited to access the correct file paths. 
   
This code will take hours to run if you're doing a lot of data! Plug in your computer. Also make sure you computer will not turn off while it is running (you may need to do this in your computer settings). It's ok if the screen turns off, but the computer must continue running. The model saves results at checkpoints, so if it stops for some reason, some of the data will be saved. 

To try to make it faster: One option is to open multiple instances of this notebook and run different years and/or loggers seperately. If you do this, make sure the folders labels are different for each piece that is running. 


## Run Sandhills data

This assumes the data is organized such that there is a folder for each year and each year contains folders for each logger (ie pond). 

e.g. This would be the file path for the data from logger 400 in 2022: 

`/Volumes/Expansion/Frog Call Project/Calling Data/FLSHE/FLSHE_2022/FLSHE_2022_400/`



In [40]:
# edit this if you only want to run the model for specific years/ponds
all_years = [str(x) for x in range(2017, 2023)] # choose years to analyze - e.g. range(2017, 2023) analyzes years 2017 through 2022 (DOES NOT INCLUDE LAST NUMBER!)
all_loggers = [str(x) for x in range(398, 404)] # choose logger names to analyze - e.g. range(398, 404) analyzes loggers named 398 through 403 (DOES NOT INCLUDE LAST NUMBER!)

# create a df where the indices are all all file names we want to run 
flshe_files = pd.DataFrame()
        
for i in range(0, len(all_years)):
    for j in range(0, len(all_loggers)):
        
        # folder name where data is stored
        folder = '/Volumes/Expansion/Frog Call Project/Calling Data/FLSHE/FLSHE_' + all_years[i] + '/FLSHE_' + all_years[i] + '_' + all_loggers[j] + '/*'
        
        temp = pd.DataFrame(index = glob(folder),columns=['score', 'year', 'logger']) # create dataframe for year i, logger j
        temp['year'] = all_years[i] # automatically label year for these files
        temp['logger'] = all_ponds[j] # automatically label pond for these files
        
        flshe_files = pd.concat([flshe_files, temp])
        
# run ribbit for all of the files! 
flshe_rs = flshe_files.copy()
run_ribbit_for_indices(flshe_rs, folder_lab = '_flshe')


/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 93, using nperseg = 93
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 94, using nperseg = 94
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 93, using nperseg = 93
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 94, using nperseg = 94
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/s

Time elapsed  0:00:06.636472


# Running model with Ichaway data

This assumes the data is organized such that there is a folder for each year and each year contains folders for each logger and each logger has subfolders for different dates. 

e.g. This would be the file path for the data from logger 1a in 2022 for the date 2-2-15: 

`/Volumes/Expansion/Frog Call Project/Calling Data/ichaway/ichaway_2022/1a/2-2-15`

In [36]:
all_years = [str(x) for x in range(2014, 2016)] # choose years to analyze - e.g. range(2014, 2016) analyzes loggers in years 2014 through 2015 (DOES NOT INCLUDE LAST NUMBER!)
all_loggers = ['1a','2a','3a', '4a', '5a', '6a', '7a', '8a', '9a', '10a']

# create a df where the indices are all all file names we want to run 
ich_files = pd.DataFrame()
        
for i in range(0, len(all_years)):
    for j in range(0, len(all_loggers)):
        
        # folder name where data is stored
        folder = '/Volumes/Expansion/Frog Call Project/Calling Data/ichaway/ichaway_' + all_years[i] + '/' + all_loggers[j]  + '/*/*'
        
        temp = pd.DataFrame(index = glob(folder),columns=['score', 'year', 'logger']) # create dataframe for year i, pond j
        temp['year'] = all_years[i] # automatically label year for these files
        temp['logger'] = all_loggers[j] # automatically label pond for these files
        
        ich_files = pd.concat([ich_files, temp])
        
# run ribbit for all of the files! 
ich_rs = ich_files.copy()        
run_ribbit_for_indices(ich_rs, folder_lab = '_ich')



# Example of running a OFAT Sensitivity analysis 

Using `ich_files` from above - could do same with `flshe_files`

In [100]:
# OFAT SA of all parameters - results saved to ribbit_scores folder 
warnings.filterwarnings("ignore")

ich_rs = ich_files.copy()

# SA for pulse rate 
pulse_rate_vals = [[10,28], [12,28], [14,28]] # pulse rate parameters we want to test 
run_ribbit_SA(ich_rs, test_param = "pulse_rate_range", param_vals = pulse_rate_vals) 

ich_rs.to_csv('./ribbit_scores/ichaway_pulse_rate_range_SA.csv') # save to csv


# SA for noise band 
noise_bands = [[[150,200], [1100,1200]], [[150,200], [1200,1300]]]
run_ribbit_SA(ich_rs, test_param = "noise_bands", param_vals = noise_bands)

ich_rs.to_csv('./ribbit_scores/ichaway_noise_bands_SA.csv') # save to csv


# SA for signal band 
signal_band = [[300,800], [600,1000], [300,1000]]
run_ribbit_SA(ich_rs, test_param = "signal_band", param_vals = signal_band)

ich_rs.to_csv('./ribbit_scores/ichaway_signal_band_SA.csv') # save to csv

# SA for clip duration 
clip_duration = [1.5,2]
run_ribbit_SA(ich_rs, test_param = "clip_duration", param_vals = clip_duration)

ich_rs.to_csv('./ribbit_scores/ichaway_clip_duration_SA.csv') # save to csv


# SA for window samples
window_samples = [300,400]
run_ribbit_SA(ich_rs, test_param = "window_samples", param_vals = window_samples)

ich_rs.to_csv('./ribbit_scores/ichaway_window_samples_SA.csv') # save to csv
    

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/s

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/s

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/s

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/s

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 62, using nperseg = 62
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 63, using nperseg = 63
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/s

...

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages

/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 124, using nperseg = 124
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 125, using nperseg = 125
  .format(nperseg, input_length))
/Users/mayalapp/opt/anaconda3/envs/opensoundscape060/lib/python3.7/site-packages

Time elapsed  0:28:02.761386
